In [ ]:
import pandas as pd
import numpy as np
import yfinance as yf
import statsmodels.api as sm
import matplotlib.pyplot as plt

from datetime import datetime
from google.colab import drive
from pandas_datareader import data as pdr
from sklearn.datasets import make_regression
from dateutil.relativedelta import relativedelta
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression, RidgeCV
from sklearn.metrics import accuracy_score, mean_absolute_error, mean_squared_error

drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
Training = pd.read_csv('/content/drive/MyDrive/Senior Fall/Senior Thesis/Data/Separately/Train_big.csv', converters={'Global Company Key':str})

In [ ]:
Training.drop(Training.columns[-1], axis=1, inplace=True)

In [ ]:
y_train = Training['Selected']
X_train = Training.drop(columns=['Selected'])

# Try different lambda values and select the best lambda using RidgeCV

In [ ]:
alphas = np.logspace(-4, 2, 10)  # Varying lambda values logarithmically

model = RidgeCV(alphas=alphas, scoring='neg_mean_squared_error', cv=5) # ridge_cv is already trained with the best alpha
model.fit(X_train, y_train)

best_alpha = model.alpha_
score = model.score(X_train, y_train)

print("Best alpha:", best_alpha)
print("RidgeCV Score:", score)

/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_ridge.py:216: LinAlgWarning: Ill-conditioned matrix (rcond=3.64007e-24): result may not be accurate.
  return linalg.solve(A, Xy, assume_a="pos", overwrite_a=True).T
/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_ridge.py:216: LinAlgWarning: Ill-conditioned matrix (rcond=8.59499e-24): result may not be accurate.
  return linalg.solve(A, Xy, assume_a="pos", overwrite_a=True).T
/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_ridge.py:216: LinAlgWarning: Ill-conditioned matrix (rcond=7.53416e-24): result may not be accurate.
  return linalg.solve(A, Xy, assume_a="pos", overwrite_a=True).T
/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_ridge.py:216: LinAlgWarning: Ill-conditioned matrix (rcond=8.59498e-24): result may not be accurate.
  return linalg.solve(A, Xy, assume_a="pos", overwrite_a=True).T
/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_ridge.py:216: LinAlgWarnin

Best alpha: 100.0
RidgeCV Score: 0.0006841351671257323


/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_ridge.py:216: LinAlgWarning: Ill-conditioned matrix (rcond=2.8877e-21): result may not be accurate.
  return linalg.solve(A, Xy, assume_a="pos", overwrite_a=True).T


# Run Ridge prediction with the best lambda

In [ ]:
Test = pd.read_csv('/content/drive/MyDrive/Senior Fall/Senior Thesis/Data/Separately/Test_small_filled_and_cleaned.csv', index_col=0, converters={'Global Company Key':str})

In [ ]:
predictions = model.predict(Test[X_train.columns])
Test['Selected'] = predictions

# Sort by 'Data Date' and 'Selected' and obtain Tickers of Top Quintile

In [ ]:
Test = Test.sort_values(by=['Data Date', 'Selected'], ascending = [True, False])

In [ ]:
def obtain_Ticker(group):
    return group.head(len(group) // 5)['Ticker Symbol'].tolist()

In [ ]:
# Group DataFrame by 'Data Date' and apply the custom function
Tickers = Test.groupby('Data Date').apply(obtain_Ticker)
Dates = Test['Data Date'].unique()

# Obtain Stock Price Data of Top Quintile

In [ ]:
replicating_portfolio1 = pd.DataFrame()

for i in range(350):
  print(i)
  start_date = Dates[i]

  if (i+1) < len(Dates):
    end_date = (datetime.strptime(Dates[i+1], '%Y-%m-%d') + relativedelta(days=1)).strftime('%Y-%m-%d')
  else:
    end_date = (datetime.strptime(Dates[i], '%Y-%m-%d') + relativedelta(months=1) + relativedelta(days=1)).strftime('%Y-%m-%d')

  df = pd.DataFrame()
  print(start_date)
  print(end_date)

  for ticker in Tickers[i]:
    try:
      ticker_data = yf.download(ticker, start=start_date, end=end_date)['Adj Close']
      if not ticker_data.empty:
        df[ticker] = ticker_data
        df[ticker] = df[ticker].fillna(method='ffill')
        df[ticker] = df[ticker].pct_change()
        df['Equal_Weighted_Returns'] = df.mean(axis=1)
    except Exception as e:
      print('exception e')

  if not df.empty:
    replicating_portfolio1 = pd.concat([replicating_portfolio1, df['Equal_Weighted_Returns']], axis=0)

replicating_portfolio1

0
1983-09-30
1983-11-01
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed

ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['AXRX']: Exception("%ticker%: Data doesn't exist for startDate = 433742400, endDate = 436510800")



1
1983-10-31
1983-12-01
[*********************100%%**********************]  1 of 1 completed
2
1983-11-30
1984-01-01
[*********************100%%**********************]  1 of 1 completed

ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['CCF']: Exception("%ticker%: Data doesn't exist for startDate = 439016400, endDate = 441781200")



3
1983-12-31
1984-02-01
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed

...

ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['CHND']: Exception("%ticker%: Data doesn't exist for startDate = 1348977600, endDate = 1351742400")



[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
349
2012-10-31
2012-12-01
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[******

ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['XFLS']: Exception("%ticker%: Data doesn't exist for startDate = 1351656000, endDate = 1354338000")



[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed


0
1983-09-30       NaN
1983-10-03  0.001417
1983-10-04 -0.024380
1983-10-05  0.002893
1983-10-06  0.000000
...              ...
2012-11-26 -0.008505
2012-11-27 -0.014384
2012-11-28  0.016980
2012-11-29  0.002895
2012-11-30  0.033826

[6882 rows x 1 columns]

In [ ]:
replicating_portfolio1.to_csv('Ridge_rep1.csv')

In [ ]:
replicating_portfolio2 = pd.DataFrame()

for i in range(350, len(Tickers)):
  print(i)
  start_date = Dates[i]

  if (i+1) < len(Dates):
    end_date = (datetime.strptime(Dates[i+1], '%Y-%m-%d') + relativedelta(days=1)).strftime('%Y-%m-%d')
  else:
    end_date = (datetime.strptime(Dates[i], '%Y-%m-%d') + relativedelta(months=1) + relativedelta(days=1)).strftime('%Y-%m-%d')

  df = pd.DataFrame()
  print(start_date)
  print(end_date)

  for ticker in Tickers[i]:
    try:
      ticker_data = yf.download(ticker, start=start_date, end=end_date)['Adj Close']
      if not ticker_data.empty:
        df[ticker] = ticker_data
        df[ticker] = df[ticker].fillna(method='ffill')
        df[ticker] = df[ticker].pct_change()
        df['Equal_Weighted_Returns'] = df.mean(axis=1)
    except Exception as e:
      print('exception e')

  if not df.empty:
    replicating_portfolio2 = pd.concat([replicating_portfolio2, df['Equal_Weighted_Returns']], axis=0)

replicating_portfolio2

350
2012-11-30
2013-01-01
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed

ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['NWYU']: Exception('%ticker%: No timezone found, symbol may be delisted')



[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed

ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['KDMP']: Exception('%ticker%: No timezone found, symbol may be delisted')



[*********************100%%**********************]  1 of 1 completed

...

ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['5912B']: Exception('%ticker%: No timezone found, symbol may be delisted')



478
2023-07-31
2023-09-01
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[******

ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['UAL2']: Exception('%ticker%: No timezone found, symbol may be delisted')



[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%******

0
2012-11-30       NaN
2012-12-03 -0.005908
2012-12-04 -0.003883
2012-12-05 -0.012662
2012-12-06  0.011163
...              ...
2023-10-24  0.004626
2023-10-25 -0.014316
2023-10-26  0.003193
2023-10-27 -0.017420
2023-10-30  0.005401

[2839 rows x 1 columns]

In [ ]:
replicating_portfolio2.to_csv('Ridge_rep2.csv')

In [ ]:
#rep1 = pd.read_csv('Ridge_rep1.csv')
#rep2 = pd.read_csv('Ridge_rep2.csv')

rep1 = pd.read_csv('/content/drive/MyDrive/Senior Fall/Senior Thesis/Data/Separately/Ridge_rep1.csv')
rep2 = pd.read_csv('/content/drive/MyDrive/Senior Fall/Senior Thesis/Data/Separately/Ridge_rep2.csv')

In [ ]:
rep = pd.concat([rep1, rep2])
rep = rep.rename(columns ={'0': 'returns'})
rep = rep.dropna()
rep

Unnamed: 0   returns
1     1983-10-03  0.001417
2     1983-10-04 -0.024380
3     1983-10-05  0.002893
4     1983-10-06  0.000000
5     1983-10-07  0.007184
...          ...       ...
2834  2023-10-24  0.004626
2835  2023-10-25 -0.014316
2836  2023-10-26  0.003193
2837  2023-10-27 -0.017420
2838  2023-10-30  0.005401

[9269 rows x 2 columns]

In [ ]:
rep.to_csv('Ridge_replicating.csv', index=False)